In [1]:
# pip install selenium
# pip install webdriver-manager

In [1]:
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.chrome.service import Service as ChromeService
from webdriver_manager.chrome import ChromeDriverManager
from selenium.webdriver.chrome.options import Options
import time


In [2]:
# # Set up Chrome options to open developer tools by default
# chrome_options = Options()
# chrome_options.add_argument("--auto-open-devtools-for-tabs")
# chrome_options.add_experimental_option("devtools.open", True)
# chrome_options.add_argument("--auto-open-devtools-tab=network")

# Set up Chrome options
chrome_options = Options()
chrome_options.add_argument("--auto-open-devtools-for-tabs")  # Opens DevTools
chrome_options.add_argument("--remote-allow-origins=*")  # Handle potential CORS errors
chrome_options.set_capability("goog:loggingPrefs", {"performance": "ALL"})


# Set up the Selenium WebDriver with Chrome options
service = ChromeService(executable_path=ChromeDriverManager().install())
driver = webdriver.Chrome(service=service, options=chrome_options)

# Open the TradingView login page
login_url = 'https://www.tradingview.com/accounts/signin/'
driver.get(login_url)

In [3]:
# Allow the page to load completely
time.sleep(5)

# Locate and click the "Email" button using XPath
email_button_xpath = '/html/body/div[3]/div/div/div[1]/div/div/div[2]/div/div/button'
email_button = driver.find_element(By.XPATH, email_button_xpath)
email_button.click()

# Allow time for the next page to load
time.sleep(3)

# Locate the username and password fields using XPath
username_field = driver.find_element(By.XPATH, '//*[@id="id_username"]')
password_field = driver.find_element(By.XPATH, '//*[@id="id_password"]')

# Input the username and password
username_field.send_keys('bitcoincovid1993')
password_field.send_keys('Ilovemahadev@143')

In [6]:
import json

# Allow time for the login process
time.sleep(5)

# Check if login was successful by looking for a specific element or URL
if 'Your Dashboard' in driver.page_source:
    print('Login successful')
else:
    print('Login failed')

# Optionally, navigate to another page
# dashboard_url = 'https://in.tradingview.com/chart/n2kZoeH7/?symbol=NASDAQ%3ANVDA'
dashboard_url = 'https://in.tradingview.com/chart/n2kZoeH7/?symbol=NYSE%3ADD'
driver.get(dashboard_url)

# Fetch performance logs to capture WebSocket connections
logs = driver.get_log("performance")

# Initialize variable to store the first response
volume_footprint_raw_data = ""


# Parse logs to find WebSocket traffic
for log_entry in logs:
    log = json.loads(log_entry["message"])
    message = log["message"]
    method = message.get("method")

    # # Check for WebSocket events
    # if method in ["Network.webSocketCreated", "Network.webSocketFrameSent", "Network.webSocketFrameReceived"]:
    #     print(json.dumps(message, indent=4))

    # Check for WebSocket events
    # if method in ["Network.webSocketFrameReceived"]:
    #     print(json.dumps(message, indent=4))

    # Check for WebSocketFrameReceived events
    if method == "Network.webSocketFrameReceived":
        params = message.get("params", {})
        response = params.get("response", {})
        payload_data = response.get("payloadData", "")

        # # Filter messages that contain 'extendTo' in payloadData
        # if "extendTo" in payload_data:
        #     print(json.dumps(message, indent=4))

        # Filter messages that contain 'extendTo' in payloadData
        if "footprint" in payload_data and "buyVolume" in payload_data and "extendTo" in payload_data:
            volume_footprint_raw_data = json.dumps(message, indent=4)
            break

# Allow time for the page to load
time.sleep(5)

# Save the page source to a text file
page_source = driver.page_source
with open('page_source.txt', 'w', encoding='utf-8') as file:
    file.write(page_source)

Login failed


In [7]:
with open('volume_footprint_raw_data.txt', 'w', encoding='utf-8') as file:
    file.write(volume_footprint_raw_data)

In [ ]:
import re
import json

# Path to the uploaded file
file_path = 'volume_footprint_raw_data.txt'

# Read the file content
with open(file_path, 'r', encoding='utf-8') as file:
    data = file.read()

# Remove backslashes
cleaned_data = data.replace("\\", "")

# Write the cleaned data back to the file
with open("subset_volume.txt", 'w', encoding='utf-8') as file:
    if isinstance(cleaned_data, list):
        file.write("\n".join(cleaned_data))  # Join list into a string with line breaks
    else:
        file.write(cleaned_data)  # Directly write if already a string
print("Cleaned data successfully written to subset_volume.txt.")


# # Read the file content
# with open(file_path, 'r', encoding='utf-8') as file:
#     data = file.read()

Cleaned data successfully written to subset_volume.txt.


In [11]:
# Read the file content
with open("subset_volume.txt", 'r', encoding='utf-8') as file:
    cleaned_data = file.read()

In [ ]:
# # Sanitize the data to remove extra spaces
# cleaned_data = [item.strip() for item in cleaned_data]

# # Count the number of occurrences of "erase"
# erase_count = cleaned_data.count("erase")
# print(f"Number of occurrences of 'erase': {erase_count}")

# # Find the first and last occurrence indices of "erase"
# try:
#     if erase_count > 0:
#         # First occurrence
#         first_index = cleaned_data.index("erase")
#         print(f"First occurrence of 'erase': {first_index}")
        
#         # Last occurrence
#         last_index = len(cleaned_data) - cleaned_data[::-1].index("erase") - 1
#         print(f"Last occurrence of 'erase': {last_index}")
#     else:
#         print("'erase' not found in cleaned_data.")
# except ValueError as e:
#     print(f"Error: {e}")


Number of occurrences of 'erase': 0
'erase' not found in cleaned_data.


In [14]:
# Assuming cleaned_data is a list
try:
    # Find the index of "footprintLevels"
    start_index = cleaned_data.index("footprintLevels") - 2
    print(start_index)
    start_index = max(0, start_index)  # Ensure it doesn't go below 0

    # Find the last occurrence of "erase"
    # end_index = cleaned_data[::-1].index("erase")  # Find from reversed list
    end_index = cleaned_data.index("erase") - 2
    print(end_index)
    # end_index = len(cleaned_data) - end_index - 2  # Convert to the correct index


    # Count the number of occurrences of "erase"
    erase_count = cleaned_data.count("erase")
    print(f"Number of occurrences of 'erase': {erase_count}")

    indexes = [i for i in range(len(cleaned_data)) if cleaned_data.startswith("erase", i)]

    # Print the indexes
    print(f"Indexes of occurrences of 'erase': {indexes}")

    # # Find the end_index based on the last occurrence
    # try:
    #     if erase_count > 0:
    #         # Get the last occurrence of 'erase'
    #         end_index = len(cleaned_data) - cleaned_data[::-1].index("erase") - 2
    #         print(f"End index based on the last occurrence of 'erase': {end_index}")
    #     else:
    #         print("'erase' not found in cleaned_data.")
    # except ValueError:
    #     print("'erase' not found in cleaned_data.")
    # Subset from start_index to end_index (exclusive)
    subset = cleaned_data[start_index:end_index]
    print(f"Subset of cleaned_data from index {start_index} to {end_index}: {subset}")
except ValueError as e:
    print(f"Error: {e}")

366
1770499
Number of occurrences of 'erase': 1
Indexes of occurrences of 'erase': [1770501]
Subset of cleaned_data from index 366 to 1770499: {"footprintLevels":[{"data":[{"id":4,"startIndex":1,"type":"buy","price":86.04,"extendTo":2},{"id":5,"startIndex":1,"type":"buy","price":86.06,"extendTo":2},{"id":6,"startIndex":1,"type":"buy","price":86.08,"extendTo":2},{"id":14,"startIndex":6,"type":"buy","price":86.2,"extendTo":7},{"id":21,"startIndex":9,"type":"buy","price":86.32000000000001,"extendTo":10},{"id":20,"startIndex":9,"type":"buy","price":86.3,"extendTo":15},{"id":27,"startIndex":14,"type":"sell","price":86.32000000000001,"extendTo":15},{"id":19,"startIndex":9,"type":"buy","price":86.28,"extendTo":16},{"id":28,"startIndex":14,"type":"sell","price":86.34,"extendTo":16},{"id":18,"startIndex":9,"type":"buy","price":86.26,"extendTo":17},{"id":29,"startIndex":14,"type":"sell","price":86.38,"extendTo":22},{"id":44,"startIndex":26,"type":"buy","price":86.52,"extendTo":27},{"id":43,"star

In [ ]:
# try:
#     # Assuming cleaned_data is a list of strings
#     # Find the index of "footprintLevels"
#     start_index = cleaned_data.index("footprintLevels") - 2
#     start_index = max(0, start_index)  # Ensure it doesn't go below 0
#     print(f"Start index: {start_index}")

#     # Count the number of occurrences of "erase"
#     erase_count = cleaned_data.count("erase")
#     print(f"Number of occurrences of 'erase': {erase_count}")

#     # Find all indexes of "erase"
#     indexes = [i for i in range(len(cleaned_data)) if cleaned_data.startswith("erase", i)]
#     print(f"Indexes of occurrences of 'erase': {indexes}")

#     # Determine the end_index based on the last occurrence
#     if erase_count > 0:
#         # Get the last occurrence of 'erase' (corrected logic)
#         last_erase_index = len(cleaned_data) - cleaned_data[::-1].index("erase") - 5
#         end_index = min(len(cleaned_data), last_erase_index)  # Ensure it doesn't exceed the length
#         print(f"End index based on the last occurrence of 'erase': {end_index}")

#         # Subset from start_index to end_index (exclusive)
#         subset = cleaned_data[start_index:end_index]
#         print(f"Subset of cleaned_data from index {start_index} to {end_index}: {subset}")
#     else:
#         print("'erase' not found in cleaned_data. No subset created.")

# except ValueError as e:
#     print(f"Error: {e}")

Start index: 137896
Number of occurrences of 'erase': 2
Indexes of occurrences of 'erase': [137005, 2305360]
Error: substring not found


In [20]:
# Write the cleaned data back to the file
with open("subset_volume.txt", 'w', encoding='utf-8') as file:
    file.write(cleaned_data)

In [ ]:
import pandas as pd

nested_data = json.loads(subset)

footprint_levels = nested_data['footprintLevels']
df = pd.DataFrame(footprint_levels[0]['data'])

footprints = nested_data['footprints']

df1 = pd.DataFrame(footprints[0]['data'])


In [19]:
df

id  startIndex  type  price  extendTo
0        4           1   buy  86.04       2.0
1        5           1   buy  86.06       2.0
2        6           1   buy  86.08       2.0
3       14           6   buy  86.20       7.0
4       21           9   buy  86.32      10.0
...    ...         ...   ...    ...       ...
4235  7244        3118  sell  83.06       NaN
4236  7245        3118  sell  83.08       NaN
4237  7246        3118  sell  83.10       NaN
4238  7247        3118  sell  83.12       NaN
4239  7428        3186  sell  82.62       NaN

[4240 rows x 5 columns]

In [20]:
df1

id  index    poc    val    vah  \
0        2      0  86.01  85.96  86.02   
1        3      1  86.09  86.06  86.10   
2        7      2  86.09  86.08  86.10   
3        8      3  86.07  86.06  86.10   
4        9      4  86.11  86.10  86.12   
...    ...    ...    ...    ...    ...   
3191  7433   3191  82.29  82.24  82.30   
3192  7434   3192  82.25  82.20  82.30   
3193  7435   3193  82.11  82.10  82.14   
3194  7436   3194  82.13  82.08  82.14   
3195  7437   3195  82.05  82.04  82.06   

                                                 levels  
0     [{'buyVolume': 10.0, 'sellVolume': 150.0, 'imb...  
1     [{'buyVolume': 9.0, 'sellVolume': 0.0, 'imbala...  
2     [{'buyVolume': 200.0, 'sellVolume': 0.0, 'imba...  
3     [{'buyVolume': 134.0, 'sellVolume': 0.0, 'imba...  
4     [{'buyVolume': 0.0, 'sellVolume': 98.0, 'imbal...  
...                                                 ...  
3191  [{'buyVolume': 124.0, 'sellVolume': 0.0, 'imba...  
3192  [{'buyVolume': 536.0, 'sellVolume': 146.0, 'im...  
3193  [{'buyVolume': 0.0, 'sellVolume': 375.0, 'imba...  
3194  [{'buyVolume': 934.0, 'sellVolume': 811.0, 'im...  
3195  [{'buyVolume': 4406.0, 'sellVolume': 1510.0, '...  

[3196 rows x 6 columns]

In [30]:
from datetime import datetime, timezone, timedelta

start_index = cleaned_data.index("t_ms") - 2
subset = cleaned_data[start_index:]
print(subset)
end_index = subset.index("}") 

start_index = subset.index("t_ms") + 6

timestamp_utc_string = subset[start_index:end_index]



# Convert the UTC timestamp string to datetime object
timestamp_ms = int(timestamp_utc_string)  # Convert to integer
timestamp_sec = timestamp_ms / 1000  # Convert to seconds

# Convert to UTC datetime
utc_datetime = datetime.fromtimestamp(timestamp_sec, tz=timezone.utc)

# Convert to EST by subtracting 5 hours from UTC
est_offset = timedelta(hours=-5)
est_datetime = utc_datetime + est_offset

# Format as string
est_datetime_str = est_datetime.strftime('%Y-%m-%d %H:%M:%S')

# Print the result
print("EST Datetime:", est_datetime_str)

,"t_ms":1733873065101}"
        },
        "timestamp": 266874.718388
    }
}
EST Datetime: 2024-12-10 18:24:25


In [31]:
tradingview_df = pd.read_csv('tradingview_links.csv')

In [51]:
import re
import json
import pandas as pd


for idx in range(0,len(tradingview_df)):
    ticker = tradingview_df.loc[idx,'Symbol']
    dashboard_url = tradingview_df.loc[idx,'TradingView Link']

    driver.get(dashboard_url)

    # Fetch performance logs to capture WebSocket connections
    logs = driver.get_log("performance")

    # Initialize variable to store the first response
    volume_footprint_raw_data = ""
    # Parse logs to find WebSocket traffic
    for log_entry in logs:
        log = json.loads(log_entry["message"])
        message = log["message"]
        method = message.get("method")

        # Check for WebSocketFrameReceived events
        if method == "Network.webSocketFrameReceived":
            params = message.get("params", {})
            response = params.get("response", {})
            payload_data = response.get("payloadData", "")

            # Filter messages that contain 'extendTo' in payloadData
            if "footprint" in payload_data and "buyVolume" in payload_data and "extendTo" in payload_data:
                volume_footprint_raw_data = json.dumps(message, indent=4)
                break

    # Allow time for the page to load
    time.sleep(5)

    with open('volume_footprint_raw_data.txt', 'w', encoding='utf-8') as file:
        file.write(volume_footprint_raw_data)

    # Path to the uploaded file
    file_path = 'volume_footprint_raw_data.txt'

    # Read the file content
    with open(file_path, 'r', encoding='utf-8') as file:
        data = file.read()

    # Remove backslashes
    cleaned_data = data.replace("\\", "")

    # Write the cleaned data back to the file
    with open("subset_volume.txt", 'w', encoding='utf-8') as file:
        if isinstance(cleaned_data, list):
            file.write("\n".join(cleaned_data))  # Join list into a string with line breaks
        else:
            file.write(cleaned_data)  # Directly write if already a string
    print("Cleaned data successfully written to subset_volume.txt.")

    # Read the file content
    with open("subset_volume.txt", 'r', encoding='utf-8') as file:
        cleaned_data = file.read()

    # Assuming cleaned_data is a list
    try:
        # Find the index of "footprintLevels"
        start_index = cleaned_data.index("footprintLevels") - 2
        print(start_index)
        start_index = max(0, start_index)  # Ensure it doesn't go below 0

        # cleaned_data = cleaned_data[start_index:]

        # Find the last occurrence of "erase"
        # end_index = cleaned_data[::-1].index("erase")  # Find from reversed list
        end_index = cleaned_data.index("erase") - 2
        print(end_index)
        # end_index = len(cleaned_data) - end_index - 2  # Convert to the correct index


        # Count the number of occurrences of "erase"
        erase_count = cleaned_data.count("erase")
        print(f"Number of occurrences of 'erase': {erase_count}")

        indexes = [i for i in range(len(cleaned_data)) if cleaned_data.startswith("erase", i)]

        # Print the indexes
        print(f"Indexes of occurrences of 'erase': {indexes}")
        
        subset = cleaned_data[start_index:end_index]
        print(f"Subset of cleaned_data from index {start_index} to {end_index}: {subset}")
    except ValueError as e:
        print(f"Error: {e}")

    # # Write the cleaned data back to the file
    # with open("subset_volume.txt", 'w', encoding='utf-8') as file:
    #     file.write(cleaned_data)

    # # Write the cleaned data back to the file
    # with open("subset_volume_data.txt", 'w', encoding='utf-8') as file:
    #     file.write(subset)
    
    nested_data = json.loads(subset)

    footprint_levels = nested_data['footprintLevels']
    df = pd.DataFrame(footprint_levels[0]['data'])

    footprints = nested_data['footprints']

    df1 = pd.DataFrame(footprints[0]['data'])

    print(df.head())

Cleaned data successfully written to subset_volume.txt.
41340
1902565
Number of occurrences of 'erase': 1
Indexes of occurrences of 'erase': [1902567]
Subset of cleaned_data from index 41340 to 1902565: {"footprintLevels":[{"data":[{"id":5,"startIndex":1,"type":"buy","price":82.72,"extendTo":2},{"id":6,"startIndex":1,"type":"buy","price":82.74,"extendTo":2},{"id":14,"startIndex":3,"type":"buy","price":82.88,"extendTo":4},{"id":15,"startIndex":3,"type":"buy","price":82.9,"extendTo":4},{"id":16,"startIndex":3,"type":"buy","price":82.92,"extendTo":4},{"id":17,"startIndex":3,"type":"buy","price":82.94,"extendTo":4},{"id":18,"startIndex":3,"type":"buy","price":82.96000000000001,"extendTo":4},{"id":4,"startIndex":1,"type":"buy","price":82.7,"extendTo":5},{"id":9,"startIndex":3,"type":"buy","price":82.76,"extendTo":5},{"id":10,"startIndex":3,"type":"buy","price":82.78,"extendTo":5},{"id":11,"startIndex":3,"type":"buy","price":82.8,"extendTo":5},{"id":12,"startIndex":3,"type":"buy","price":82.

JSONDecodeError: Expecting value: line 1 column 1 (char 0)

In [46]:
# Read the file content
with open("subset_volume.txt", 'r', encoding='utf-8') as file:
    cleaned_data = file.read()

# Assuming cleaned_data is a list
try:
    # Find the index of "footprintLevels"
    start_index = cleaned_data.index("footprintLevels") - 2
    print(start_index)
    start_index = max(0, start_index)  # Ensure it doesn't go below 0

    # cleaned_data = cleaned_data[start_index:]

    # Find the last occurrence of "erase"
    # end_index = cleaned_data[::-1].index("erase")  # Find from reversed list
    end_index = cleaned_data.index("erase") - 2
    print(end_index)
    # end_index = len(cleaned_data) - end_index - 2  # Convert to the correct index


    # Count the number of occurrences of "erase"
    erase_count = cleaned_data.count("erase")
    print(f"Number of occurrences of 'erase': {erase_count}")

    indexes = [i for i in range(len(cleaned_data)) if cleaned_data.startswith("erase", i)]

    # Print the indexes
    print(f"Indexes of occurrences of 'erase': {indexes}")
    
    subset = cleaned_data[start_index:end_index]
    print(f"Subset of cleaned_data from index {start_index} to {end_index}: {subset}")
except ValueError as e:
    print(f"Error: {e}")

374
1863305
Number of occurrences of 'erase': 1
Indexes of occurrences of 'erase': [1863307]
Subset of cleaned_data from index 374 to 1863305: {"footprintLevels":[{"data":[{"id":11,"startIndex":5,"type":"buy","price":135.92000000000002,"extendTo":6},{"id":12,"startIndex":5,"type":"buy","price":135.96,"extendTo":6},{"id":13,"startIndex":5,"type":"buy","price":136.0,"extendTo":6},{"id":15,"startIndex":6,"type":"buy","price":136.12,"extendTo":7},{"id":16,"startIndex":6,"type":"buy","price":136.16,"extendTo":7},{"id":17,"startIndex":6,"type":"buy","price":136.2,"extendTo":7},{"id":4,"startIndex":1,"type":"sell","price":136.56,"extendTo":8},{"id":5,"startIndex":1,"type":"sell","price":136.6,"extendTo":8},{"id":6,"startIndex":1,"type":"sell","price":136.64000000000001,"extendTo":9},{"id":23,"startIndex":11,"type":"buy","price":136.56,"extendTo":12},{"id":24,"startIndex":11,"type":"buy","price":136.6,"extendTo":12},{"id":25,"startIndex":11,"type":"buy","price":136.64000000000001,"extendTo":12

In [47]:
# Write the cleaned data back to the file
with open("subset_data.txt", 'w', encoding='utf-8') as file:
    file.write(subset)

with open("subset_data.txt", 'r', encoding='utf-8') as file:
    subset = file.read()

In [48]:
nested_data = json.loads(subset)

In [ ]:
MMM,https://in.tradingview.com/chart/n2kZoeH7/?symbol=NYSE%3AMMM
TRV,https://in.tradingview.com/chart/n2kZoeH7/?symbol=NYSE%3ATRV
META,https://in.tradingview.com/chart/n2kZoeH7/?symbol=NASDAQ%3AMETA
DD,https://in.tradingview.com/chart/n2kZoeH7/?symbol=NYSE%3ADD
NKE,https://in.tradingview.com/chart/n2kZoeH7/?symbol=NYSE%3ANKE
IBM,https://in.tradingview.com/chart/n2kZoeH7/?symbol=NYSE%3AIBM
CVS,https://in.tradingview.com/chart/n2kZoeH7/?symbol=NYSE%3ACVS
MSFT,https://in.tradingview.com/chart/n2kZoeH7/?symbol=NASDAQ%3AMSFT
UNH,https://in.tradingview.com/chart/n2kZoeH7/?symbol=NYSE%3AUNH
AXP,https://in.tradingview.com/chart/n2kZoeH7/?symbol=NYSE%3AAXP
TSLA,https://in.tradingview.com/chart/n2kZoeH7/?symbol=NASDAQ%3ATSLA
NVDA,https://in.tradingview.com/chart/n2kZoeH7/?symbol=NASDAQ%3ANVDA
CAT,https://in.tradingview.com/chart/n2kZoeH7/?symbol=NYSE%3ACAT
VZ,https://in.tradingview.com/chart/n2kZoeH7/?symbol=NYSE%3AVZ
WMT,https://in.tradingview.com/chart/n2kZoeH7/?symbol=NYSE%3AWMT
HD,https://in.tradingview.com/chart/n2kZoeH7/?symbol=NYSE%3AHD
PG,https://in.tradingview.com/chart/n2kZoeH7/?symbol=NYSE%3APG
V,https://in.tradingview.com/chart/n2kZoeH7/?symbol=NYSE%3AV
MRK,https://in.tradingview.com/chart/n2kZoeH7/?symbol=NYSE%3AMRK
BA,https://in.tradingview.com/chart/n2kZoeH7/?symbol=NYSE%3ABA
DIS,https://in.tradingview.com/chart/n2kZoeH7/?symbol=NYSE%3ADIS
GS,https://in.tradingview.com/chart/n2kZoeH7/?symbol=NYSE%3AGS
JPM,https://in.tradingview.com/chart/n2kZoeH7/?symbol=NYSE%3AJPM
KO,https://in.tradingview.com/chart/n2kZoeH7/?symbol=NYSE%3AKO
GE,https://in.tradingview.com/chart/n2kZoeH7/?symbol=NYSE%3AGE
CSCO,https://in.tradingview.com/chart/n2kZoeH7/?symbol=NASDAQ%3ACSCO
PFE,https://in.tradingview.com/chart/n2kZoeH7/?symbol=NYSE%3APFE
JNJ,https://in.tradingview.com/chart/n2kZoeH7/?symbol=NYSE%3AJNJ
AMZN,https://in.tradingview.com/chart/n2kZoeH7/?symbol=NASDAQ%3AAMZN
CVX,https://in.tradingview.com/chart/n2kZoeH7/?symbol=NYSE%3ACVX
XOM,https://in.tradingview.com/chart/n2kZoeH7/?symbol=NYSE%3AXOM
AAPL,https://in.tradingview.com/chart/n2kZoeH7/?symbol=NASDAQ%3AAAPL
MCD,https://in.tradingview.com/chart/n2kZoeH7/?symbol=NYSE%3AMCD
INTC,https://in.tradingview.com/chart/n2kZoeH7/?symbol=NASDAQ%3AINTC